In [78]:
import numpy as np
import pandas as pd


train_X = pd.read_csv("X_train.csv")
test_X = pd.read_csv("X_test.csv")
train_y = pd.read_csv("y_train.csv")

train_X.isnull().sum()

id                             0
name                           0
has_test                       0
response_letter_required       0
salary_from                 4032
salary_currency                0
salary_gross                 148
published_at                   0
created_at                     0
employer_name                  0
description                    1
area_id                        0
area_name                      0
dtype: int64

In [79]:
train_X['salary_gross'].value_counts()

salary_gross
False    18726
True      9060
Name: count, dtype: int64

In [80]:
train_X['salary_from'] = train_X['salary_from'].fillna(0)
train_X['description'] = train_X['description'].fillna('')
train_X['salary_gross'] = train_X['salary_gross'].fillna(False)

In [81]:
import spacy


nlp = spacy.load("ru_core_news_lg")

In [82]:
df = train_y.merge(train_X)

In [83]:
import re

i = 0
for desr in test_X['description']:
	pattern = re.compile('<.*?>|&([a-z0-9]+|#[0-9]{1,6}|#x[0-9a-f]{1,6});')
	desr = re.sub(pattern, '', desr)
	desr = desr.lower()
	test_X['description'][i] = desr
	i += 1
	
i = 0
for desr in df['description']:
	pattern = re.compile('<.*?>|&([a-z0-9]+|#[0-9]{1,6}|#x[0-9a-f]{1,6});')
	desr = re.sub(pattern, '', desr)
	desr = desr.lower()
	df['description'][i] = desr
	i += 1

/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3737238416.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_X['description'][i] = desr
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3737238416.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test_X['description'][i] = desr
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3737238416.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-

In [84]:
df['description_vectors'] = df['description'].apply(lambda x: nlp(x).vector)

# Создание отдельных столбцов для каждой компоненты вектора
df[['vector_dim_' + str(i) for i in range(df['description_vectors'][0].shape[0])]] = (
	pd.DataFrame(df['description_vectors'].to_list(), index=df.index))

# Удаление столбца с векторами текста
df = df.drop('description_vectors', axis=1)
df.info()

/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3630359406.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[['vector_dim_' + str(i) for i in range(df['description_vectors'][0].shape[0])]] = (
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3630359406.py:4: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[['vector_dim_' + str(i) for i in range(df['description_vectors'][0].shape[0])]] = (
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3630359406.py:4: PerformanceWarning: Da

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27934 entries, 0 to 27933
Columns: 314 entries, id to vector_dim_299
dtypes: bool(3), float32(300), float64(2), int64(2), object(7)
memory usage: 34.4+ MB


In [85]:
test_X['description_vectors'] = test_X['description'].apply(lambda x: nlp(x).vector)
test_X[['vector_dim_' + str(i) for i in range(test_X['description_vectors'][0].shape[0])]] = (
	pd.DataFrame(test_X['description_vectors'].to_list(), index=test_X.index))

# Удаление столбца с векторами текста
test_X = test_X.drop('description_vectors', axis=1)
test_X.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9312 entries, 0 to 9311
Columns: 313 entries, id to vector_dim_299
dtypes: bool(2), float32(300), float64(1), int64(2), object(8)
memory usage: 11.5+ MB


/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3896147928.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_X[['vector_dim_' + str(i) for i in range(test_X['description_vectors'][0].shape[0])]] = (
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3896147928.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  test_X[['vector_dim_' + str(i) for i in range(test_X['description_vectors'][0].shape[0])]] = (
/var/folders/s1/d77vpf9x71g30l8xyk06nxvr0000gn/T/ipykernel_67785/3896147928.py:2: Perfor

In [113]:
from catboost import CatBoostRegressor, Pool

X = ['name', 'salary_from', 'area_id']
for i in range(300):
	X.append('vector_dim_' + str(i))
cat_features = ['name']
y = ['salary_to']

In [114]:
model = CatBoostRegressor(
	cat_features=cat_features,
	eval_metric='SMAPE',
	learning_rate=0.03,
	random_seed=42,
	verbose=100,
	iterations=6000
)

from sklearn.model_selection import train_test_split

train, test = train_test_split(df, test_size=0.2, random_state=42)

train_pool = Pool(df[X], df[y], cat_features=cat_features)
dev_pool = Pool(test[X], test[y], cat_features=cat_features)

model.fit(train_pool, eval_set=dev_pool)

0:	learn: 59.8029934	test: 59.5382392	best: 59.5382392 (0)	total: 53.9ms	remaining: 5m 23s
100:	learn: 33.4588491	test: 32.7187274	best: 32.7187274 (100)	total: 2.18s	remaining: 2m 7s
200:	learn: 29.8117401	test: 27.1448624	best: 27.1448624 (200)	total: 3.95s	remaining: 1m 53s
300:	learn: 28.5801575	test: 26.3128835	best: 26.3082501 (297)	total: 5.57s	remaining: 1m 45s
400:	learn: 27.5214229	test: 25.5480862	best: 25.5453857 (399)	total: 7.68s	remaining: 1m 47s
500:	learn: 26.7009144	test: 24.8754431	best: 24.8754431 (500)	total: 9.33s	remaining: 1m 42s
600:	learn: 26.1113544	test: 24.4985003	best: 24.4930323 (597)	total: 11s	remaining: 1m 38s
700:	learn: 25.5211118	test: 24.0636676	best: 24.0636676 (700)	total: 12.7s	remaining: 1m 35s
800:	learn: 25.0983307	test: 23.7750788	best: 23.7750788 (800)	total: 14.4s	remaining: 1m 33s
900:	learn: 24.6848320	test: 23.4120188	best: 23.4120188 (900)	total: 16.1s	remaining: 1m 31s
1000:	learn: 24.3023529	test: 23.1617771	best: 23.1560894 (992)	to

In [115]:
predict = model.predict(test_X[X])
submit_id = test_X.id.to_list()
result = pd.DataFrame({'id': submit_id, 'salary_to': np.round(predict)})
result.to_csv('submission.csv', index=False)